# Backtrader

- Run through all examples in [QuickStart Guide](https://www.backtrader.com/docu/quickstart/quickstart/#from-0-to-100-the-samples).
- Test out codes for [Momentum-Based Strategy Optimization with Grid Search on Backtrader](https://medium.com/funny-ai-quant/momentum-based-strategy-optimization-with-grid-search-on-backtrader-8c0d6cd1cc36)


In [10]:
import backtrader as bt
from backtrader.feeds import PandasData
from datetime import datetime
import os
import sys
import pandas as pd
from pathlib import Path
import random
import matplotlib.pyplot as plt
repo_dir = Path.cwd().as_posix()

if repo_dir not in sys.path:
    sys.path.append(repo_dir)

%load_ext autoreload
%autoreload 2
%matplotlib inline

from src import utils

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Basic Setup


In [2]:
cerebro = bt.Cerebro()

print("Starting Portfolio Value: %.2f" % cerebro.broker.getvalue())

cerebro.run()

print("Final Portfolio Value: %.2f" % cerebro.broker.getvalue())

Starting Portfolio Value: 10000.00
Final Portfolio Value: 10000.00


## Setting Cash


In [3]:
cerebro = bt.Cerebro()
cerebro.broker.setcash(1000000)

print("Starting Portfolio Value: %.2f" % cerebro.broker.getvalue())

cerebro.run()

print("Final Portfolio Value: %.2f" % cerebro.broker.getvalue())

Starting Portfolio Value: 1000000.00
Final Portfolio Value: 1000000.00


## DataFeed

| Info                                   | Details                                                                                                                                                                                                                                                    |
| -------------------------------------- | ---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------- |
| yfinance to download data              | &bull; Unable to download Yahoo Finance data directly using YahooFinanceData since it is outdated.                                                                                                                                                         |
| Can't access data feed before backtest | &bull; Data feed is processed sequentially during backtest i.e. datafeed is initialized but does not contain any 'current' bar of data to access. <br>&bull; data feed becomes available only during execution of backtest (inside methods like 'next()'). |
| current bar = index 0                  | &bull; Cannot access positive index i.e. future values. <br>&bull; past values by negative index. Previous day -> index -1. 2 days ago -> index -2                                                                                                         |
| Standard lines                         | &bull; Inherited from 'AbstractDataBase'. <br>&bull; close, low, high, open, volume, openinterest, and datetime. <br>&bull; Inherit [`PandasData`](https://www.backtrader.com/docu/dataautoref/#pandasdata) define custom lines.                           |
| Set datetime index                     | &bull; If index is not datetime (i.e. strings), Need to convert index to pd.DatetimeIndex. <br>&bull; If datetime is a column and of datetime type, need to specify index of datetime column or set index to -1 for Backtrader to infer location.          |


In [2]:
df = utils.load_df()
df

open        high         low       close        volume
datetime                                                                
2008-01-02    7.116786    7.152143    6.876786    6.958571  1.079179e+09
2008-01-03    6.978929    7.049643    6.881786    6.961786  8.420664e+08
2008-01-04    6.837500    6.892857    6.388929    6.430357  1.455832e+09
2008-01-07    6.473214    6.557143    6.079643    6.344286  2.072193e+09
2008-01-08    6.433571    6.516429    6.100000    6.116071  1.523816e+09
...                ...         ...         ...         ...           ...
2025-01-17  232.119995  232.289993  228.479996  229.979996  6.848830e+07
2025-01-21  224.000000  224.419998  219.380005  222.639999  9.807040e+07
2025-01-22  219.789993  224.119995  219.789993  223.830002  6.412650e+07
2025-01-23  224.740005  227.029999  222.300003  223.660004  6.023480e+07
2025-01-24  224.779999  225.630005  221.410004  222.779999  5.461950e+07

[4294 rows x 5 columns]

In [126]:
class TestStrategy(bt.Strategy):
    def next(self):
        print(f"\nlen(self.data) : {len(self.data)}")
        print(f"Current Date: {self.data.datetime.date(0)}")
        print(f"Current Close: {self.data.close[0]}")
        print(f"Current Volume : {self.data.volume[0]}")

        # Access previous bar's data
        if len(self.data) > 1:  # Ensure there is at least one previous bar
            print(f"Previous Date: {self.data.datetime.date(-1)}")
            print(f"Previous Close: {self.data.close[-1]}")

        # Access two bars ago
        if len(self.data) > 2:  # Ensure there are at least two previous bars
            print(f"Two Bars Ago Date: {self.data.datetime.date(-2)}")
            print(f"Two Bars Ago Close: {self.data.close[-2]}")


data_feed = bt.feeds.PandasData(dataname=df)

cerebro = bt.Cerebro()
cerebro.addstrategy(TestStrategy)
cerebro.adddata(data_feed)
cerebro.broker.setcash(1000000.0)

# Print out the starting conditions
print(f"Starting Portfolio Value: {cerebro.broker.getvalue()}")

# Run over everything
cerebro.run()

# Print out the final result
print(f"Final Portfolio Value: {cerebro.broker.getvalue()}")

Starting Portfolio Value: 1000000.0

len(self.data) : 1
Current Date: 2008-01-02
Current Close: 6.958570957183838
Current Volume : 1079178800.0

len(self.data) : 2
Current Date: 2008-01-03
Current Close: 6.961785793304443
Current Volume : 842066400.0
Previous Date: 2008-01-02
Previous Close: 6.958570957183838

len(self.data) : 3
Current Date: 2008-01-04
Current Close: 6.430356979370117
Current Volume : 1455832000.0
Previous Date: 2008-01-03
Previous Close: 6.961785793304443
Two Bars Ago Date: 2008-01-02
Two Bars Ago Close: 6.958570957183838

len(self.data) : 4
Current Date: 2008-01-07
Current Close: 6.34428596496582
Current Volume : 2072193200.0
Previous Date: 2008-01-04
Previous Close: 6.430356979370117
Two Bars Ago Date: 2008-01-03
Two Bars Ago Close: 6.961785793304443

len(self.data) : 5
Current Date: 2008-01-08
Current Close: 6.116071224212647
Current Volume : 1523816000.0
Previous Date: 2008-01-07
Previous Close: 6.34428596496582
Two Bars Ago Date: 2008-01-04
Two Bars Ago Close: 6

## Custom Data Feed

- Create class to inherit from PandasData.
- Ensure line object is the same as the column in DataFrame (i.e. case sensitive).


In [117]:
from backtrader.feeds import PandasData


class CustomPandasData(PandasData):
    # Add a new line for the custom column
    lines = ("test",)

    # Map the custom column to its position or name in the DataFrame
    params = (("test", -1),)  # -1 means it will autodetect by column name

In [130]:
# Create custom column/signal i.e. 'test'
if "test" not in df.columns:
    df["test"] = [random.randint(1, 10) for _ in range(len(df))]


class TestStrategy(bt.Strategy):
    def next(self):
        print(f"\nlen(self.data) : {len(self.data)}")
        print(f"Current Date: {self.data.datetime.date(0)}")
        print(f"Current Close: {self.data.close[0]}")
        print(f"Current Volume : {self.data.volume[0]}")
        print(f"Current test : {self.data.test[0]}")

        # Access previous bar's data
        if len(self.data) > 1:  # Ensure there is at least one previous bar
            print(f"Previous Date: {self.data.datetime.date(-1)}")
            print(f"Previous Close: {self.data.close[-1]}")

        # Access two bars ago
        if len(self.data) > 2:  # Ensure there are at least two previous bars
            print(f"Two Bars Ago Date: {self.data.datetime.date(-2)}")
            print(f"Two Bars Ago Close: {self.data.close[-2]}")


# Use the custom data feed
data_feed = CustomPandasData(dataname=df)

cerebro = bt.Cerebro()
cerebro.addstrategy(TestStrategy)
cerebro.adddata(data_feed)
cerebro.broker.setcash(1000000.0)

# Print out the starting conditions
print(f"Starting Portfolio Value: {cerebro.broker.getvalue()}")

# Run over everything
cerebro.run()

# Print out the final result
print(f"Final Portfolio Value: {cerebro.broker.getvalue()}")

Starting Portfolio Value: 1000000.0

len(self.data) : 1
Current Date: 2008-01-02
Current Close: 6.958570957183838
Current Volume : 1079178800.0
Current test : 2.0

len(self.data) : 2
Current Date: 2008-01-03
Current Close: 6.961785793304443
Current Volume : 842066400.0
Current test : 3.0
Previous Date: 2008-01-02
Previous Close: 6.958570957183838

len(self.data) : 3
Current Date: 2008-01-04
Current Close: 6.430356979370117
Current Volume : 1455832000.0
Current test : 4.0
Previous Date: 2008-01-03
Previous Close: 6.961785793304443
Two Bars Ago Date: 2008-01-02
Two Bars Ago Close: 6.958570957183838

len(self.data) : 4
Current Date: 2008-01-07
Current Close: 6.34428596496582
Current Volume : 2072193200.0
Current test : 3.0
Previous Date: 2008-01-04
Previous Close: 6.430356979370117
Two Bars Ago Date: 2008-01-03
Two Bars Ago Close: 6.961785793304443

len(self.data) : 5
Current Date: 2008-01-08
Current Close: 6.116071224212647
Current Volume : 1523816000.0
Current test : 7.0
Previous Date: 

## Create Buy

- 'self.buy' generate order but unknown if executed, when and at what price.
- Default sizer = 1
- Default order type = MOO
- No commission computed.
- No timeframe implied - bars can represent 1 min, 1 hour, 1 day, 1 week or any other time period.


In [131]:
class TestStrategy(bt.Strategy):

    def log(self, txt, dt=None):
        """Logging function fot this strategy"""
        dt = dt or self.datas[0].datetime.date(0)
        print("%s, %s" % (dt.isoformat(), txt))

    def __init__(self):
        # Keep a reference to the "close" line in the data[0] dataseries
        self.dataclose = self.datas[0].close

    def next(self):
        # Simply log the closing price of the series from the reference
        self.log("Close, %.2f" % self.dataclose[0])

        if self.dataclose[0] < self.dataclose[-1]:
            # current close less than previous close

            if self.dataclose[-1] < self.dataclose[-2]:
                # previous close less than the previous close

                # BUY, BUY, BUY!!! (with all possible default parameters)
                self.log("BUY CREATE, %.2f" % self.dataclose[0])
                self.buy()


# Use the custom data feed
data_feed = bt.feeds.PandasData(dataname=df)

cerebro = bt.Cerebro()
cerebro.addstrategy(TestStrategy)
cerebro.adddata(data_feed)
cerebro.broker.setcash(1000000.0)

# Print out the starting conditions
print(f"Starting Portfolio Value: {cerebro.broker.getvalue()}")

# Run over everything
cerebro.run()

# Print out the final result
print(f"Final Portfolio Value: {cerebro.broker.getvalue()}")

Starting Portfolio Value: 1000000.0
2008-01-02, Close, 6.96
2008-01-02, BUY CREATE, 6.96
2008-01-03, Close, 6.96
2008-01-04, Close, 6.43
2008-01-07, Close, 6.34
2008-01-07, BUY CREATE, 6.34
2008-01-08, Close, 6.12
2008-01-08, BUY CREATE, 6.12
2008-01-09, Close, 6.41
2008-01-10, Close, 6.36
2008-01-11, Close, 6.17
2008-01-11, BUY CREATE, 6.17
2008-01-14, Close, 6.39
2008-01-15, Close, 6.04
2008-01-16, Close, 5.70
2008-01-16, BUY CREATE, 5.70
2008-01-17, Close, 5.75
2008-01-18, Close, 5.76
2008-01-22, Close, 5.56
2008-01-23, Close, 4.97
2008-01-23, BUY CREATE, 4.97
2008-01-24, Close, 4.84
2008-01-24, BUY CREATE, 4.84
2008-01-25, Close, 4.64
2008-01-25, BUY CREATE, 4.64
2008-01-28, Close, 4.64
2008-01-29, Close, 4.70
2008-01-30, Close, 4.72
2008-01-31, Close, 4.83
2008-02-01, Close, 4.78
2008-02-04, Close, 4.70
2008-02-04, BUY CREATE, 4.70
2008-02-05, Close, 4.62
2008-02-05, BUY CREATE, 4.62
2008-02-06, Close, 4.36
2008-02-06, BUY CREATE, 4.36
2008-02-07, Close, 4.33
2008-02-07, BUY CREAT

## Create Sell


In [132]:
# Create a Stratey
class TestStrategy(bt.Strategy):

    def log(self, txt, dt=None):
        """Logging function fot this strategy"""
        dt = dt or self.datas[0].datetime.date(0)
        print("%s, %s" % (dt.isoformat(), txt))

    def __init__(self):
        # Keep a reference to the "close" line in the data[0] dataseries
        self.dataclose = self.datas[0].close

        # To keep track of pending orders
        self.order = None

    def notify_order(self, order):
        if order.status in [order.Submitted, order.Accepted]:
            # Buy/Sell order submitted/accepted to/by broker - Nothing to do
            return

        # Check if an order has been completed
        # Attention: broker could reject order if not enough cash
        if order.status in [order.Completed]:
            if order.isbuy():
                self.log("BUY EXECUTED, %.2f" % order.executed.price)
            elif order.issell():
                self.log("SELL EXECUTED, %.2f" % order.executed.price)

            self.bar_executed = len(self)

        elif order.status in [order.Canceled, order.Margin, order.Rejected]:
            self.log("Order Canceled/Margin/Rejected")

        # Write down: no pending order
        self.order = None

    def next(self):
        # Simply log the closing price of the series from the reference
        self.log("Close, %.2f" % self.dataclose[0])

        # Check if an order is pending ... if yes, we cannot send a 2nd one
        if self.order:
            return

        # Check if we are in the market
        if not self.position:

            # Not yet ... we MIGHT BUY if ...
            if self.dataclose[0] < self.dataclose[-1]:
                # current close less than previous close

                if self.dataclose[-1] < self.dataclose[-2]:
                    # previous close less than the previous close

                    # BUY, BUY, BUY!!! (with default parameters)
                    self.log("BUY CREATE, %.2f" % self.dataclose[0])

                    # Keep track of the created order to avoid a 2nd order
                    self.order = self.buy()

        else:

            # Already in the market ... we might sell
            if len(self) >= (self.bar_executed + 5):
                # SELL, SELL, SELL!!! (with all possible default parameters)
                self.log("SELL CREATE, %.2f" % self.dataclose[0])

                # Keep track of the created order to avoid a 2nd order
                self.order = self.sell()


# Use the custom data feed
data_feed = bt.feeds.PandasData(dataname=df)

cerebro = bt.Cerebro()
cerebro.addstrategy(TestStrategy)
cerebro.adddata(data_feed)
cerebro.broker.setcash(1000000.0)

# Print out the starting conditions
print(f"Starting Portfolio Value: {cerebro.broker.getvalue()}")

# Run over everything
cerebro.run()

# Print out the final result
print(f"Final Portfolio Value: {cerebro.broker.getvalue()}")

Starting Portfolio Value: 1000000.0
2008-01-02, Close, 6.96
2008-01-02, BUY CREATE, 6.96
2008-01-03, BUY EXECUTED, 6.98
2008-01-03, Close, 6.96
2008-01-04, Close, 6.43
2008-01-07, Close, 6.34
2008-01-08, Close, 6.12
2008-01-09, Close, 6.41
2008-01-10, Close, 6.36
2008-01-10, SELL CREATE, 6.36
2008-01-11, SELL EXECUTED, 6.29
2008-01-11, Close, 6.17
2008-01-11, BUY CREATE, 6.17
2008-01-14, BUY EXECUTED, 6.34
2008-01-14, Close, 6.39
2008-01-15, Close, 6.04
2008-01-16, Close, 5.70
2008-01-17, Close, 5.75
2008-01-18, Close, 5.76
2008-01-22, Close, 5.56
2008-01-22, SELL CREATE, 5.56
2008-01-23, SELL EXECUTED, 4.86
2008-01-23, Close, 4.97
2008-01-23, BUY CREATE, 4.97
2008-01-24, BUY EXECUTED, 5.00
2008-01-24, Close, 4.84
2008-01-25, Close, 4.64
2008-01-28, Close, 4.64
2008-01-29, Close, 4.70
2008-01-30, Close, 4.72
2008-01-31, Close, 4.83
2008-01-31, SELL CREATE, 4.83
2008-02-01, SELL EXECUTED, 4.87
2008-02-01, Close, 4.78
2008-02-04, Close, 4.70
2008-02-04, BUY CREATE, 4.70
2008-02-05, BUY E

## Commission

- Final portfolio value calculated by broker takes into account the 'close' on 24 Jan 2025.
- Actual execution price would be next trading day opening. Hence the discrepancy.


In [134]:
# Create a Stratey
class TestStrategy(bt.Strategy):

    def log(self, txt, dt=None):
        """Logging function fot this strategy"""
        dt = dt or self.datas[0].datetime.date(0)
        print("%s, %s" % (dt.isoformat(), txt))

    def __init__(self):
        # Keep a reference to the "close" line in the data[0] dataseries
        self.dataclose = self.datas[0].close

        # To keep track of pending orders and buy price/commission
        self.order = None
        self.buyprice = None
        self.buycomm = None

    def notify_order(self, order):
        if order.status in [order.Submitted, order.Accepted]:
            # Buy/Sell order submitted/accepted to/by broker - Nothing to do
            return

        # Check if an order has been completed
        # Attention: broker could reject order if not enough cash
        if order.status in [order.Completed]:
            if order.isbuy():
                self.log(
                    "BUY EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f"
                    % (order.executed.price, order.executed.value, order.executed.comm)
                )

                self.buyprice = order.executed.price
                self.buycomm = order.executed.comm
            else:  # Sell
                self.log(
                    "SELL EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f"
                    % (order.executed.price, order.executed.value, order.executed.comm)
                )

            self.bar_executed = len(self)

        elif order.status in [order.Canceled, order.Margin, order.Rejected]:
            self.log("Order Canceled/Margin/Rejected")

        self.order = None

    def notify_trade(self, trade):
        if not trade.isclosed:
            return

        self.log("OPERATION PROFIT, GROSS %.2f, NET %.2f" % (trade.pnl, trade.pnlcomm))

    def next(self):
        # Simply log the closing price of the series from the reference
        self.log("Close, %.2f" % self.dataclose[0])

        # Check if an order is pending ... if yes, we cannot send a 2nd one
        if self.order:
            return

        # Check if we are in the market
        if not self.position:

            # Not yet ... we MIGHT BUY if ...
            if self.dataclose[0] < self.dataclose[-1]:
                # current close less than previous close

                if self.dataclose[-1] < self.dataclose[-2]:
                    # previous close less than the previous close

                    # BUY, BUY, BUY!!! (with default parameters)
                    self.log("BUY CREATE, %.2f" % self.dataclose[0])

                    # Keep track of the created order to avoid a 2nd order
                    self.order = self.buy()

        else:

            # Already in the market ... we might sell
            if len(self) >= (self.bar_executed + 5):
                # SELL, SELL, SELL!!! (with all possible default parameters)
                self.log("SELL CREATE, %.2f" % self.dataclose[0])

                # Keep track of the created order to avoid a 2nd order
                self.order = self.sell()


# Use the custom data feed
data_feed = bt.feeds.PandasData(dataname=df)

cerebro = bt.Cerebro()
cerebro.addstrategy(TestStrategy)
cerebro.adddata(data_feed)
cerebro.broker.setcash(1000000.0)

# Set the commission - 0.1% ... divide by 100 to remove the %
cerebro.broker.setcommission(commission=0.001)

# Print out the starting conditions
print(f"Starting Portfolio Value: {cerebro.broker.getvalue()}")

# Run over everything
cerebro.run()

# Print out the final result
print(f"Final Portfolio Value: {cerebro.broker.getvalue()}")

Starting Portfolio Value: 1000000.0
2008-01-02, Close, 6.96
2008-01-02, BUY CREATE, 6.96
2008-01-03, BUY EXECUTED, Price: 6.98, Cost: 6.98, Comm 0.01
2008-01-03, Close, 6.96
2008-01-04, Close, 6.43
2008-01-07, Close, 6.34
2008-01-08, Close, 6.12
2008-01-09, Close, 6.41
2008-01-10, Close, 6.36
2008-01-10, SELL CREATE, 6.36
2008-01-11, SELL EXECUTED, Price: 6.29, Cost: 6.98, Comm 0.01
2008-01-11, OPERATION PROFIT, GROSS -0.69, NET -0.71
2008-01-11, Close, 6.17
2008-01-11, BUY CREATE, 6.17
2008-01-14, BUY EXECUTED, Price: 6.34, Cost: 6.34, Comm 0.01
2008-01-14, Close, 6.39
2008-01-15, Close, 6.04
2008-01-16, Close, 5.70
2008-01-17, Close, 5.75
2008-01-18, Close, 5.76
2008-01-22, Close, 5.56
2008-01-22, SELL CREATE, 5.56
2008-01-23, SELL EXECUTED, Price: 4.86, Cost: 6.34, Comm 0.00
2008-01-23, OPERATION PROFIT, GROSS -1.48, NET -1.49
2008-01-23, Close, 4.97
2008-01-23, BUY CREATE, 4.97
2008-01-24, BUY EXECUTED, Price: 5.00, Cost: 5.00, Comm 0.00
2008-01-24, Close, 4.84
2008-01-25, Close, 4

## Parameters + Sizing


In [9]:
# Create a Stratey
class TestStrategy(bt.Strategy):
    params = (("exitbars", 5),)

    def log(self, txt, dt=None):
        """Logging function fot this strategy"""
        dt = dt or self.datas[0].datetime.date(0)
        print("%s, %s" % (dt.isoformat(), txt))

    def __init__(self):
        # Keep a reference to the "close" line in the data[0] dataseries
        self.dataclose = self.datas[0].close

        # To keep track of pending orders and buy price/commission
        self.order = None
        self.buyprice = None
        self.buycomm = None

    def notify_order(self, order):
        if order.status in [order.Submitted, order.Accepted]:
            # Buy/Sell order submitted/accepted to/by broker - Nothing to do
            return

        # Check if an order has been completed
        # Attention: broker could reject order if not enough cash
        if order.status in [order.Completed]:
            if order.isbuy():
                self.log(
                    "BUY EXECUTED, Size: %.2f, Price: %.2f, Cost: %.2f, Comm %.2f"
                    % (
                        order.executed.size,
                        order.executed.price,
                        order.executed.value,
                        order.executed.comm,
                    )
                )

                self.buyprice = order.executed.price
                self.buycomm = order.executed.comm
            else:  # Sell
                self.log(
                    "SELL EXECUTED, Size: %.2f, Price: %.2f, Cost: %.2f, Comm %.2f"
                    % (
                        order.executed.size,
                        order.executed.price,
                        order.executed.value,
                        order.executed.comm,
                    )
                )

            self.bar_executed = len(self)

        elif order.status in [order.Canceled, order.Margin, order.Rejected]:
            self.log("Order Canceled/Margin/Rejected")

        self.order = None

    def notify_trade(self, trade):
        if not trade.isclosed:
            return

        self.log("OPERATION PROFIT, GROSS %.2f, NET %.2f" % (trade.pnl, trade.pnlcomm))

    def next(self):
        # Simply log the closing price of the series from the reference
        self.log("Close, %.2f" % self.dataclose[0])

        # Check if an order is pending ... if yes, we cannot send a 2nd one
        if self.order:
            return

        # Buy even if have existing position
        if self.dataclose[0] < self.dataclose[-1]:
            # current close less than previous close

            if self.dataclose[-1] < self.dataclose[-2]:
                # previous close less than the previous close

                # BUY, BUY, BUY!!! (with default parameters)
                self.log("BUY CREATE, %.2f" % self.dataclose[0])

                # Keep track of the created order to avoid a 2nd order
                self.order = self.buy()

        # Check if we are in the market
        if self.position:

            # Already in the market ... we might sell
            if len(self) >= (self.bar_executed + self.params.exitbars):
                # SELL, SELL, SELL!!! (with all possible default parameters)
                self.log("SELL CREATE, %.2f" % self.dataclose[0])

                # Keep track of the created order to avoid a 2nd order
                self.order = self.sell()


# Use the custom data feed
data_feed = bt.feeds.PandasData(dataname=df)

cerebro = bt.Cerebro()
cerebro.addstrategy(TestStrategy)
cerebro.adddata(data_feed)
cerebro.broker.setcash(1000000.0)
cerebro.broker.setcommission(commission=0.001)

# Add a FixedSize sizer according to the stake
cerebro.addsizer(bt.sizers.FixedSize, stake=10)

# Print out the starting conditions
print(f"Starting Portfolio Value: {cerebro.broker.getvalue()}")

# Run over everything
cerebro.run()

# Print out the final result
print(f"Final Portfolio Value: {cerebro.broker.getvalue()}")

Starting Portfolio Value: 1000000.0
2008-01-02, Close, 6.96
2008-01-02, BUY CREATE, 6.96
2008-01-03, BUY EXECUTED, Size: 10.00, Price: 6.98, Cost: 69.79, Comm 0.07
2008-01-03, Close, 6.96
2008-01-04, Close, 6.43
2008-01-07, Close, 6.34
2008-01-07, BUY CREATE, 6.34
2008-01-08, BUY EXECUTED, Size: 10.00, Price: 6.43, Cost: 64.34, Comm 0.06
2008-01-08, Close, 6.12
2008-01-08, BUY CREATE, 6.12
2008-01-09, BUY EXECUTED, Size: 10.00, Price: 6.12, Cost: 61.18, Comm 0.06
2008-01-09, Close, 6.41
2008-01-10, Close, 6.36
2008-01-11, Close, 6.17
2008-01-11, BUY CREATE, 6.17
2008-01-14, BUY EXECUTED, Size: 10.00, Price: 6.34, Cost: 63.40, Comm 0.06
2008-01-14, Close, 6.39
2008-01-15, Close, 6.04
2008-01-16, Close, 5.70
2008-01-16, BUY CREATE, 5.70
2008-01-17, BUY EXECUTED, Size: 10.00, Price: 5.77, Cost: 57.68, Comm 0.06
2008-01-17, Close, 5.75
2008-01-18, Close, 5.76
2008-01-22, Close, 5.56
2008-01-23, Close, 4.97
2008-01-23, BUY CREATE, 4.97
2008-01-24, BUY EXECUTED, Size: 10.00, Price: 5.00, Cos

## Add Indicators + Plot


In [12]:
# Create a Stratey
class TestStrategy(bt.Strategy):
    params = (("maperiod", 15),)

    def log(self, txt, dt=None):
        """Logging function fot this strategy"""
        dt = dt or self.datas[0].datetime.date(0)
        print("%s, %s" % (dt.isoformat(), txt))

    def __init__(self):
        # Keep a reference to the "close" line in the data[0] dataseries
        self.dataclose = self.datas[0].close

        # To keep track of pending orders and buy price/commission
        self.order = None
        self.buyprice = None
        self.buycomm = None

        # Add a MovingAverageSimple indicator
        self.sma = bt.indicators.SimpleMovingAverage(
            self.datas[0], period=self.params.maperiod
        )

    def notify_order(self, order):
        if order.status in [order.Submitted, order.Accepted]:
            # Buy/Sell order submitted/accepted to/by broker - Nothing to do
            return

        # Check if an order has been completed
        # Attention: broker could reject order if not enough cash
        if order.status in [order.Completed]:
            if order.isbuy():
                self.log(
                    "BUY EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f"
                    % (order.executed.price, order.executed.value, order.executed.comm)
                )

                self.buyprice = order.executed.price
                self.buycomm = order.executed.comm
            else:  # Sell
                self.log(
                    "SELL EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f"
                    % (order.executed.price, order.executed.value, order.executed.comm)
                )

            self.bar_executed = len(self)

        elif order.status in [order.Canceled, order.Margin, order.Rejected]:
            self.log("Order Canceled/Margin/Rejected")

        self.order = None

    def notify_trade(self, trade):
        if not trade.isclosed:
            return

        self.log("OPERATION PROFIT, GROSS %.2f, NET %.2f" % (trade.pnl, trade.pnlcomm))

    def next(self):
        # Simply log the closing price of the series from the reference
        self.log("Close, %.2f" % self.dataclose[0])

        # Check if an order is pending ... if yes, we cannot send a 2nd one
        if self.order:
            return

        # Check if we are in the market
        if not self.position:

            # Not yet ... we MIGHT BUY if ...
            if self.dataclose[0] > self.sma[0]:

                # BUY, BUY, BUY!!! (with all possible default parameters)
                self.log("BUY CREATE, %.2f" % self.dataclose[0])

                # Keep track of the created order to avoid a 2nd order
                self.order = self.buy()

        else:

            if self.dataclose[0] < self.sma[0]:
                # SELL, SELL, SELL!!! (with all possible default parameters)
                self.log("SELL CREATE, %.2f" % self.dataclose[0])

                # Keep track of the created order to avoid a 2nd order
                self.order = self.sell()


# Use the custom data feed
data_feed = bt.feeds.PandasData(dataname=df)

cerebro = bt.Cerebro(stdstats=True)
cerebro.addstrategy(TestStrategy)
cerebro.adddata(data_feed)
cerebro.broker.setcash(1000000.0)
cerebro.broker.setcommission(commission=0.001)

# Add a FixedSize sizer according to the stake
cerebro.addsizer(bt.sizers.FixedSize, stake=10)

# Print out the starting conditions
print(f"Starting Portfolio Value: {cerebro.broker.getvalue()}")

# Run over everything
cerebro.run()

# Print out the final result
print(f"Final Portfolio Value: {cerebro.broker.getvalue()}")

Starting Portfolio Value: 1000000.0
2008-01-23, Close, 4.97
2008-01-24, Close, 4.84
2008-01-25, Close, 4.64
2008-01-28, Close, 4.64
2008-01-29, Close, 4.70
2008-01-30, Close, 4.72
2008-01-31, Close, 4.83
2008-02-01, Close, 4.78
2008-02-04, Close, 4.70
2008-02-05, Close, 4.62
2008-02-06, Close, 4.36
2008-02-07, Close, 4.33
2008-02-08, Close, 4.48
2008-02-11, Close, 4.62
2008-02-12, Close, 4.46
2008-02-13, Close, 4.62
2008-02-14, Close, 4.55
2008-02-15, Close, 4.45
2008-02-19, Close, 4.36
2008-02-20, Close, 4.42
2008-02-21, Close, 4.34
2008-02-22, Close, 4.27
2008-02-25, Close, 4.28
2008-02-26, Close, 4.26
2008-02-27, Close, 4.39
2008-02-28, Close, 4.64
2008-02-28, BUY CREATE, 4.64
2008-02-29, BUY EXECUTED, Price: 4.62, Cost: 46.17, Comm 0.05
2008-02-29, Close, 4.47
2008-03-03, Close, 4.35
2008-03-03, SELL CREATE, 4.35
2008-03-04, SELL EXECUTED, Price: 4.36, Cost: 46.17, Comm 0.04
2008-03-04, OPERATION PROFIT, GROSS -2.61, NET -2.70
2008-03-04, Close, 4.45
2008-03-04, BUY CREATE, 4.45
20

<IPython.core.display.Javascript object>

[[<Figure size 640x480 with 4 Axes>]]

## Optimize


In [9]:
# Create a Stratey
class TestStrategy(bt.Strategy):
    params = (
        ("maperiod", 15),
        ("printlog", False),
    )

    def log(self, txt, dt=None, doprint=False):
        """Logging function fot this strategy"""
        if self.params.printlog or doprint:
            dt = dt or self.datas[0].datetime.date(0)
            print("%s, %s" % (dt.isoformat(), txt))

    def __init__(self):
        # Keep a reference to the "close" line in the data[0] dataseries
        self.dataclose = self.datas[0].close

        # To keep track of pending orders and buy price/commission
        self.order = None
        self.buyprice = None
        self.buycomm = None

        # Add a MovingAverageSimple indicator
        self.sma = bt.indicators.SimpleMovingAverage(
            self.datas[0], period=self.params.maperiod
        )

    def notify_order(self, order):
        if order.status in [order.Submitted, order.Accepted]:
            # Buy/Sell order submitted/accepted to/by broker - Nothing to do
            return

        # Check if an order has been completed
        # Attention: broker could reject order if not enough cash
        if order.status in [order.Completed]:
            if order.isbuy():
                self.log(
                    "BUY EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f"
                    % (order.executed.price, order.executed.value, order.executed.comm)
                )

                self.buyprice = order.executed.price
                self.buycomm = order.executed.comm
            else:  # Sell
                self.log(
                    "SELL EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f"
                    % (order.executed.price, order.executed.value, order.executed.comm)
                )

            self.bar_executed = len(self)

        elif order.status in [order.Canceled, order.Margin, order.Rejected]:
            self.log("Order Canceled/Margin/Rejected")

        # Write down: no pending order
        self.order = None

    def notify_trade(self, trade):
        if not trade.isclosed:
            return

        self.log("OPERATION PROFIT, GROSS %.2f, NET %.2f" % (trade.pnl, trade.pnlcomm))

    def next(self):
        # Simply log the closing price of the series from the reference
        self.log("Close, %.2f" % self.dataclose[0])

        # Check if an order is pending ... if yes, we cannot send a 2nd one
        if self.order:
            return

        # Check if we are in the market
        if not self.position:

            # Not yet ... we MIGHT BUY if ...
            if self.dataclose[0] > self.sma[0]:

                # BUY, BUY, BUY!!! (with all possible default parameters)
                self.log("BUY CREATE, %.2f" % self.dataclose[0])

                # Keep track of the created order to avoid a 2nd order
                self.order = self.buy()

        else:

            if self.dataclose[0] < self.sma[0]:
                # SELL, SELL, SELL!!! (with all possible default parameters)
                self.log("SELL CREATE, %.2f" % self.dataclose[0])

                # Keep track of the created order to avoid a 2nd order
                self.order = self.sell()

    def stop(self):
        self.log(
            "(MA Period %2d) Ending Value %.2f"
            % (self.params.maperiod, self.broker.getvalue()),
            doprint=True,
        )


# Use the custom data feed
data_feed = bt.feeds.PandasData(dataname=df)

cerebro = bt.Cerebro()
# Add a strategy
strats = cerebro.optstrategy(TestStrategy, maperiod=range(10, 31))

cerebro.adddata(data_feed)
cerebro.broker.setcash(1000000.0)
cerebro.broker.setcommission(commission=0.001)

# Add a FixedSize sizer according to the stake
cerebro.addsizer(bt.sizers.FixedSize, stake=10)

# Run over everything
cerebro.run(maxcpus=1)

2025-01-24, (MA Period 10) Ending Value 1001196.45
2025-01-24, (MA Period 11) Ending Value 1001546.11
2025-01-24, (MA Period 12) Ending Value 1001846.10
2025-01-24, (MA Period 13) Ending Value 1001944.15
2025-01-24, (MA Period 14) Ending Value 1001617.10
2025-01-24, (MA Period 15) Ending Value 1001723.09
2025-01-24, (MA Period 16) Ending Value 1001829.47
2025-01-24, (MA Period 17) Ending Value 1001916.51
2025-01-24, (MA Period 18) Ending Value 1001939.52
2025-01-24, (MA Period 19) Ending Value 1001989.55
2025-01-24, (MA Period 20) Ending Value 1002052.99
2025-01-24, (MA Period 21) Ending Value 1001959.97
2025-01-24, (MA Period 22) Ending Value 1001843.05
2025-01-24, (MA Period 23) Ending Value 1002017.29
2025-01-24, (MA Period 24) Ending Value 1001909.73
2025-01-24, (MA Period 25) Ending Value 1001804.97
2025-01-24, (MA Period 26) Ending Value 1001810.59
2025-01-24, (MA Period 27) Ending Value 1001563.41
2025-01-24, (MA Period 28) Ending Value 1001502.65
2025-01-24, (MA Period 29) Endi

[[<backtrader.cerebro.OptReturn at 0x7ad6be3396a0>],